## Part 1. Creating a 8x3x8 autoencoder

In [87]:
import numpy as np
import os
import itertools
import pandas as pd

Note: for another class I'm taking concurrently (Stanford CS 230), I wrote some functions to build a simple neural net from scratch for an early homework assignment. I'm recycling those helper functions I've already made here below.

In [3]:
def layer_sizes(X, Y, n_h):
    """
    Arguments:
    X -- input dataset of shape (input size, number of examples)
    Y -- labels of shape (output size, number of examples)
    n_h -- the desired size of the hidden layer
    
    Returns:
    n_x -- the size of the input layer
    n_h -- the size of the hidden layer
    n_y -- the size of the output layer
    """
    n_x = X.shape[0] # size of input layer
    n_h = n_h #size of hidden layer--for the 8x3x8 encoder, I want this number to be 3.
    n_y = Y.shape[0] # size of output layer
    return (n_x, n_h, n_y)

In [4]:
def initialize_parameters(n_x, n_h, n_y):
    """
    Argument:
    n_x -- size of the input layer
    n_h -- size of the hidden layer
    n_y -- size of the output layer
    
    Returns:
    params -- python dictionary containing your parameters:
                    W1 -- weight matrix of shape (n_h, n_x)
                    b1 -- bias vector of shape (n_h, 1)
                    W2 -- weight matrix of shape (n_y, n_h)
                    b2 -- bias vector of shape (n_y, 1)
    """
    #I'm randomizing my weights to break symmetry but also multiplying it by 0.01 to avoid exploding gradients/make it run faster.
    np.random.seed(1)
    
    W1 = np.random.randn(n_h, n_x)*0.01
    b1 = np.zeros((n_h, 1))
    W2 = np.random.randn(n_y, n_h)*0.01
    b2 = np.zeros((n_y, 1))
    
    parameters = {"W1": W1,
                  "b1": b1,
                  "W2": W2,
                  "b2": b2}
    
    return parameters

In [5]:
#activation function I will be using for all my neurons in my encoder

def sigmoid(z):
    """
    Compute the sigmoid of z
    Arguments:
    z -- A scalar or numpy array of any size.
    Return:
    s -- sigmoid(z)
    """
    s = (1+np.exp(-z))**(-1)
    
    return s

In [6]:
def forward_propagation(X, parameters):
    """
    Argument:
    X -- input data of size (n_x, m)
    parameters -- python dictionary containing your parameters (output of initialization function)
    
    Returns:
    A2 -- The sigmoid output of the second activation
    cache -- a dictionary containing "Z1", "A1", "Z2" and "A2"
    """
    # Retrieve each parameter from the dictionary "parameters"
    W1 = parameters["W1"]
    b1 = parameters["b1"]
    W2 = parameters["W2"]
    b2 = parameters["b2"]
    
    # Implement Forward Propagation
    Z1 = np.dot(W1, X) + b1
    A1 = sigmoid(Z1) #sigmoid activation function for Z1
    Z2 = np.dot(W2, A1) + b2
    A2 = sigmoid(Z2) #sigmoid activation function for Z2
    
    cache = {"Z1": Z1,
             "A1": A1,
             "Z2": Z2,
             "A2": A2}
    
    return A2, cache

I chose to use cross-entropy for this task because I want my values to be as close to 0 or 1 as possible, and cross-entropy tends to maximize the odds of values being pushed to either of these extremes, unlike MSE which would equally allow for a distribution between 0 and 1. In this way, I'm wanting my output to look more like a classification task (where the outputs are either 0 or 1) rather than a regression task (where my outputs can RANGE between 0 and 1).

In [7]:
def compute_cost(A2, Y):
    """
    Computes the cost function (cross-entropy)
    
    Arguments:
    A2 -- The sigmoid output of the second activation, of shape (1, number of examples)
    Y -- "true" labels vector of shape (1, number of examples)

    Returns:
    cost -- cross-entropy cost
    
    """
    
    m = Y.shape[1] # number of example

    # Compute the cost function
    
    #cost = np.square(np.subtract(A2,Y)).mean() -- I wrote this in case I decide to change to MSE later on
    logprobs = np.multiply(np.log(A2),Y) + np.multiply(np.log(1-A2),(1-Y))
    cost = -(1/m)*np.sum(logprobs) 
    
    cost = float(np.squeeze(cost))  # makes sure cost is the dimension we expect. 
                                     
    assert(isinstance(cost, float))
    
    return cost

In [8]:
def backward_propagation(parameters, cache, X, Y):
    """
    Implement the backward propagation using the instructions above.
    
    Arguments:
    parameters -- python dictionary containing our parameters 
    cache -- a dictionary containing "Z1", "A1", "Z2" and "A2".
    X -- input data of shape 
    Y -- "true" labels vector of shape
    
    Returns:
    grads -- python dictionary containing your gradients with respect to different parameters
    """
    m = X.shape[1]
    
    # First, retrieve W1 and W2 from the dictionary "parameters".
    W1 = parameters["W1"]
    W2 = parameters["W2"]
        
    # Retrieve also A1 and A2 from dictionary "cache".
    A1 = cache["A1"]
    A2 = cache["A2"]
    
    # Backward propagation: calculate dW1, db1, dW2, db2. 
    dZ2 = A2 - Y
    dW2 = (1/m)*np.dot(dZ2, A1.T)
    db2 = (1/m)*np.sum(dZ2, axis = 1, keepdims = True)
    dZ1 = np.dot(W2.T,dZ2)*(A1*(1-A1)) #note: the (A1*(1-A1)) is the gradient/derivative for the sigmoid activation function
    dW1 = (1/m)*np.dot(dZ1,X.T)
    db1 = (1/m)*np.sum(dZ1, axis = 1, keepdims = True)
    
    grads = {"dW1": dW1,
             "db1": db1,
             "dW2": dW2,
             "db2": db2}
    
    return grads

In [9]:
def update_parameters(parameters, grads, learning_rate = 0.15):
    """
    Updates parameters using the gradient descent update rule given above
    
    Arguments:
    parameters -- python dictionary containing your parameters 
    grads -- python dictionary containing your gradients 
    
    Returns:
    parameters -- python dictionary containing your updated parameters 
    """
    # Retrieve each parameter from the dictionary "parameters"
    W1 = parameters["W1"]
    b1 = parameters["b1"]
    W2 = parameters["W2"]
    b2 = parameters["b2"]
    
    # Retrieve each gradient from the dictionary "grads"
    dW1 = grads["dW1"]
    db1 = grads["db1"]
    dW2 = grads["dW2"]
    db2 = grads["db2"]
    
    # Update rule for each parameter
    W1 = W1 - learning_rate*dW1
    b1 = b1 - learning_rate*db1
    W2 = W2 - learning_rate*dW2
    b2 = b2 - learning_rate*db2
    
    parameters = {"W1": W1,
                  "b1": b1,
                  "W2": W2,
                  "b2": b2}
    
    return parameters

In [10]:
def nn_model(X, Y, n_h, num_iterations = 10000, print_cost=False):
    """
    Arguments:
    X -- dataset of shape (2, number of examples)
    Y -- labels of shape (1, number of examples)
    n_h -- size of the hidden layer
    num_iterations -- Number of iterations in gradient descent loop
    print_cost -- if True, print the cost every 1000 iterations
    
    Returns:
    parameters -- parameters learnt by the model. They can then be used to predict.
    """
    
    np.random.seed(1)
    n_x = layer_sizes(X, Y, n_h)[0]
    n_y = layer_sizes(X, Y, n_h)[2]
    
    # Initialize parameters
    parameters = initialize_parameters(n_x, n_h, n_y)
    
    # Loop (gradient descent)

    for i in range(0, num_iterations):
         

        # Forward propagation
        A2, cache = forward_propagation(X, parameters)
        
        # Cost function.
        cost = compute_cost(A2, Y)
 
        # Backpropagation.
        grads = backward_propagation(parameters, cache, X, Y)
 
        # Gradient descent parameter update.
        parameters = update_parameters(parameters, grads)
        
        # Print the cost every 10000 iterations
        if print_cost and i % 10000 == 0:
            print ("Cost after iteration %i: %f" %(i, cost))

    return parameters

In [11]:
def predict(parameters, X):
    """
    Using the learned parameters, predicts a class for each example in X
    
    Arguments:
    parameters -- python dictionary containing your parameters 
    X -- input data of size (n_x, m)
    
    Returns
    predictions -- vector of predictions of our model
    """
    
    # Computes outputs using forward propagation
    A2, cache = forward_propagation(X, parameters)
    predictions = A2 #note that A2 equals the outpuit
    
    return predictions

In [12]:
#identity matrix
identity_matrix = np.array([[1, 0, 0, 0, 0, 0, 0, 0],
                          [0, 1, 0, 0, 0, 0, 0, 0],
                          [0, 0, 1, 0, 0, 0, 0, 0],
                          [0, 0, 0, 1, 0, 0, 0, 0],
                          [0, 0, 0, 0, 1, 0, 0, 0],
                          [0, 0, 0, 0, 0, 1, 0, 0],
                          [0, 0, 0, 0, 0, 0, 1, 0],
                           [0, 0, 0, 0, 0, 0, 0, 1]])
print(identity_matrix)

[[1 0 0 0 0 0 0 0]
 [0 1 0 0 0 0 0 0]
 [0 0 1 0 0 0 0 0]
 [0 0 0 1 0 0 0 0]
 [0 0 0 0 1 0 0 0]
 [0 0 0 0 0 1 0 0]
 [0 0 0 0 0 0 1 0]
 [0 0 0 0 0 0 0 1]]


In [65]:
#training my autoencoder
autoencoder_parameters = nn_model(identity_matrix, identity_matrix, 3, 100000, print_cost=True)

Cost after iteration 0: 5.543731
Cost after iteration 10000: 0.128672
Cost after iteration 20000: 0.057077
Cost after iteration 30000: 0.036587
Cost after iteration 40000: 0.026904
Cost after iteration 50000: 0.021267
Cost after iteration 60000: 0.017581
Cost after iteration 70000: 0.014982
Cost after iteration 80000: 0.013052
Cost after iteration 90000: 0.011562


In [66]:
print(autoencoder_parameters)

{'W1': array([[ 3.45178686, -4.94113013, -4.4744377 ,  4.48372364,  6.339929  ,
        -5.43077006,  4.94648878, -4.81085897],
       [-4.65112076, -4.73588252,  3.64451862, -5.91629357,  5.86900856,
         4.96689688,  4.87938375, -4.4121174 ],
       [-4.88211007, -4.72277946, -4.704304  ,  4.73574934,  6.25380154,
         4.92058384, -5.47129078,  3.45723797]]), 'b1': array([[-0.42485779],
       [-0.34359686],
       [-0.42334093]]), 'W2': array([[ 12.5807118 , -13.1297868 , -13.0960718 ],
       [-12.87776168, -12.70736866, -12.81681893],
       [-13.03548805,  12.56165693, -13.05899542],
       [ 11.10723882, -12.63233065,  11.13321926],
       [ 10.25462641,  10.12963125,  10.24239751],
       [-12.41623391,  11.09685785,  11.16454198],
       [ 11.21612624,  11.08214915, -12.43014781],
       [-13.27112819, -13.15657881,  12.6697369 ]]), 'b2': array([[ -6.20224328],
       [  5.6964804 ],
       [ -6.28072925],
       [-16.51036281],
       [-25.77641155],
       [-16.63425

In [67]:
predicted_identity = predict(autoencoder_parameters, identity_matrix)
print("Autoencoder thinks the answer is:",np.around(predicted_identity, decimals=3))
print("The ground-truth is:",identity_matrix)

Autoencoder thinks the answer is: [[0.996 0.002 0.    0.001 0.    0.    0.001 0.   ]
 [0.001 0.996 0.001 0.    0.    0.    0.    0.001]
 [0.    0.002 0.997 0.    0.    0.001 0.001 0.   ]
 [0.003 0.    0.    0.995 0.001 0.    0.    0.003]
 [0.    0.    0.    0.004 0.991 0.004 0.004 0.   ]
 [0.    0.    0.003 0.    0.001 0.995 0.    0.003]
 [0.003 0.    0.003 0.    0.001 0.    0.995 0.   ]
 [0.    0.002 0.    0.001 0.    0.001 0.    0.997]]
The ground-truth is: [[1 0 0 0 0 0 0 0]
 [0 1 0 0 0 0 0 0]
 [0 0 1 0 0 0 0 0]
 [0 0 0 1 0 0 0 0]
 [0 0 0 0 1 0 0 0]
 [0 0 0 0 0 1 0 0]
 [0 0 0 0 0 0 1 0]
 [0 0 0 0 0 0 0 1]]


My autoencoder clearly is working, as seen by the results above. Next, I have to implement a fully connected NN that predicts transcription factor binding.

My first step is to preprocess my data, which I will do by encoding all my sequences using one-hot encodings. Right now, I'm going to implement one-hot encoding using only my positive sequences. Afterwards, I'll figure out how to 1) do the same with my negative sequences 2) Augment or change all my training data to be balanced.

In [13]:
#loading in my positive examples
pathway = os.path.join('./data', 'rap1-lieb-positives.txt')
train = np.loadtxt(os.path.abspath(pathway), dtype=str)
train[0]

'ACATCCGTGCACCTCCG'

In [14]:
len(train[0])

17

In [15]:
###one-hot encoding all training examples and flattening into matrix of shape (length of sequence*length of onehot vector, m)


# all possible input values
alphabet = 'ACTG'
# define a mapping of chars to integers
char_to_int = dict((c, i) for i, c in enumerate(alphabet))
int_to_char = dict((i, c) for i, c in enumerate(alphabet))

#X = np.zeros((17*4, len(train)))
X_pos = []
for sequence in train:
    # integer encode input data
    integer_encoding = [char_to_int[char] for char in sequence]
    # one hot encode
    onehot_encoding = []
    for value in integer_encoding:
        letter = [0 for _ in range(len(alphabet))]
        letter[value] = 1
        onehot_encoding.append(letter)
    final_onehot = list(itertools.chain(*onehot_encoding))
    X_pos.append(final_onehot)
X_pos = np.array(X_pos)

In [16]:
print(X_pos[0])

[1 0 0 0 0 1 0 0 1 0 0 0 0 0 1 0 0 1 0 0 0 1 0 0 0 0 0 1 0 0 1 0 0 0 0 1 0
 1 0 0 1 0 0 0 0 1 0 0 0 1 0 0 0 0 1 0 0 1 0 0 0 1 0 0 0 0 0 1]


I'm comparing train[0] above--the sequence--to this one hot encoding and it looks correct--each "A" corresponds to the first of every 4 values being 1, "C" corresponds to the second of every 4 values being 1, etc.

Next, I need to figure out how to preprocess my negative examples. I think my strategy here will simply be to divide all the negative sequences up to be short fragments the same length as the positive examples. I can also do a quick check to make sure that none of my negative sequences match any of my positive sequences.

In [18]:
with open('./data/yeast-upstream-1k-negative.fa') as myfile:
    neg = myfile.readlines()

In [32]:
cleaned_neg = []
for line in neg:
    line = line.strip()
    if line[0] == '>':
        continue
    else:
        cleaned_neg.append(line)

In [33]:
len(cleaned_neg)

53744

In [34]:
cleaned_neg_concat = ''.join(cleaned_neg)

In [35]:
cleaned_neg_concat

'...'

In [53]:
cleaned_neg_split = [cleaned_neg_concat[i:i+17] for i in range(0, len(cleaned_neg_concat), 17)]

In [55]:
cleaned_neg_split = cleaned_neg_split[:-1]

In [59]:
overlap_with_train = []
for neg_sequence in cleaned_neg_split:
    for pos_sequence in train:
        if pos_sequence == neg_sequence:
            overlap_with_train.append(neg_sequence)
            break

In [60]:
overlap_with_train

['ACATCCGTGCACCATTT',
 'AAACCCAAACATATTAA',
 'ACCTCCGTGCATCCTGT',
 'ACACCCGTACATATTAA',
 'AGACCCATACATCACAA']

In [78]:
set_neg = set(cleaned_neg_split)
set_overlap = set(overlap_with_train)

In [80]:
set_neg = list(set_neg.difference(set_overlap))

In [66]:
'ACCTCCGTGCATCCTGT' in set_neg

False

In [68]:
###one-hot encoding my negative examples and flattening into matrix of shape (length of sequence*length of onehot vector, m)


# all possible input values
alphabet = 'ACTG'
# define a mapping of chars to integers
char_to_int = dict((c, i) for i, c in enumerate(alphabet))
int_to_char = dict((i, c) for i, c in enumerate(alphabet))

X_neg = []
for sequence in set_neg:
    # integer encode input data
    integer_encoding = [char_to_int[char] for char in sequence]
    # one hot encode
    onehot_encoding = []
    for value in integer_encoding:
        letter = [0 for _ in range(len(alphabet))]
        letter[value] = 1
        onehot_encoding.append(letter)
    final_onehot = list(itertools.chain(*onehot_encoding))
    X_neg.append(final_onehot)
X_neg = np.array(X_neg)

In [82]:
print(set_neg[0])
X_neg[0]

AACGTCCTTGCGTTTTT


array([1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 1,
       0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 0,
       0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0,
       1, 0])

In [85]:
X_pos_label = np.ones(len(X_pos))
X_neg_label = np.zeros(len(X_neg))

In [102]:
print(X_pos_label.shape)
print(X_neg_label.shape)

(137,)
(184920,)


In [88]:
X_neg

array([[1, 0, 0, ..., 0, 1, 0],
       [0, 0, 0, ..., 1, 0, 0],
       [0, 0, 1, ..., 0, 1, 0],
       ...,
       [0, 0, 0, ..., 1, 0, 0],
       [1, 0, 0, ..., 0, 0, 1],
       [0, 1, 0, ..., 1, 0, 0]])

In [89]:
X_pos

array([[1, 0, 0, ..., 0, 0, 1],
       [1, 0, 0, ..., 1, 0, 0],
       [0, 1, 0, ..., 1, 0, 0],
       ...,
       [1, 0, 0, ..., 0, 0, 0],
       [0, 0, 1, ..., 0, 1, 0],
       [1, 0, 0, ..., 1, 0, 0]])

In [105]:
np.vstack((X_neg, X_pos)).shape

(185057, 68)

In [103]:
np.hstack((X_neg_label, X_pos_label))

array([0., 0., 0., ..., 1., 1., 1.])

In [108]:
data = pd.DataFrame(np.vstack((X_neg, X_pos)))
data["label"] = np.hstack((X_neg_label, X_pos_label))

In [115]:
data

0  1  2  3  4  5  6  7  8  9  ...  59  60  61  62  63  64  65  66  67  \
0       1  0  0  0  1  0  0  0  0  1  ...   0   0   0   1   0   0   0   1   0   
1       0  0  0  1  0  0  1  0  0  0  ...   0   0   0   0   1   0   1   0   0   
2       0  0  1  0  0  1  0  0  0  0  ...   0   0   0   1   0   0   0   1   0   
3       1  0  0  0  1  0  0  0  1  0  ...   1   0   0   0   1   0   0   0   1   
4       1  0  0  0  0  1  0  0  0  0  ...   0   1   0   0   0   0   0   1   0   
...    .. .. .. .. .. .. .. .. .. ..  ...  ..  ..  ..  ..  ..  ..  ..  ..  ..   
185052  0  0  0  1  1  0  0  0  1  0  ...   0   1   0   0   0   0   1   0   0   
185053  1  0  0  0  0  1  0  0  1  0  ...   0   0   0   0   1   0   0   0   1   
185054  1  0  0  0  0  0  0  1  1  0  ...   0   1   0   0   0   1   0   0   0   
185055  0  0  1  0  1  0  0  0  1  0  ...   0   1   0   0   0   0   0   1   0   
185056  1  0  0  0  0  1  0  0  1  0  ...   0   1   0   0   0   0   1   0   0   

        label  
0         0.0  
1         0.0  
2         0.0  
3         0.0  
4         0.0  
...       ...  
185052    1.0  
185053    1.0  
185054    1.0  
185055    1.0  
185056    1.0  

[185057 rows x 69 columns]

In [120]:
data.iloc[0,68] #label

0.0

In [117]:
len(data.iloc[0,0:68].astype(np.int).values)

68

Next step: augment positive examples to be about same number as negs. Then remake data dataframe and then run neural net and be happy.

In [74]:
#loading in my negative sequences
pathway = os.path.join('./data', 'yeast-upstream-1k-negative.fa')
neg = open(os.path.abspath(pathway)).read()
neg

#now, want to figure out how to only keep the letters and nothing else.

#my_file = open("dna.txt")
#file_contents = my_file.read()
#print(file_contents)

">YAL003W 5' untranslated region, chrI 141172 - 142171, 1000 bp\nCTTCATGTCAGCCTGCACTTCTGGGTCGTTGAAGTTTCTACCGATCAAACGCTTAGCGTC\nGAAAACGGTATTCGAAGGATTCATAGCAGCTTGATTCTTAGCAGCATCACCAATCAATCT\nTTCAGTGTCAGTGAAAGCGACAAAAGATGGAGTGGTTCTGTTACCTTGATCGTTGGCAAT\nAATGTCCACACGATCATTAGCAAAGTGAGCAACACACGAGTATGTTGTACCTAAATCAAT\nACCGACAGCTTTTGACATATTATCTGTTATTTACTTGAATTTTTGTTTCTTGTAATACTT\nGATTACTTTTCTTTTGATGTGCTTATCTTACAAATAGAGAAAATAAAACAACTTAAGTAA\nGAATTGGGAAACGAAACTACAACTCAATCCCTTCTCGAAGATACATCAATCCACCCCTTA\nTATAACCTTGAAGTCCTCGAAACGATCAGCTAATCTAAATGGCCCCCCTTCTTTTTGGGT\nTCTTTCTCTCCCTTTTGCCGCCGATGGAACGTTCTGGAAAAAGAAGAATAATTTAATTAC\nTTTCTCAACTAAAATCTGGAGAAAAAACGCAAATGACAGCTTCTAAACGTTCCGTGTGCT\nTTCTTTCTAGAATGTTCTGGAAAGTTTACAACAATCCACAAGAACGAAAATGCCGTTGAC\nAATGATGAAACCATCATCCACACACCGCGCACACGTGCTTTATTTCTTTTTCTGAATTTT\nTTTTTTCCGCCATTTTCAACCAAGGAAATTTTTTTTCTTAGGGCTCAGAACCTGCAGGTG\nAAGAAGCGCTTTAGAAATCAAAGCACAACGTAACAATTTGTCGACAACCGAGCCTTTGAA\nGAAAAAATTTTTCACATTGTCGCCTCTAAATAAATAGTTTAAGGTTATCTACCCACTATA\nTTTAG

Based on this single example where I'm just comparing by eye the "real" answer and the "autoencoder" answer, I am getting fairly OK answers (1s are indeed 1s and 0s are 0.54 or below) after 100,000 epochs and a learning rate of 0.15. However, to really determine how good this is, I need to do a more robust evaluation metric. As a result, I will now implement cross-validation.

In [16]:
# Split a dataset into k folds
def cross_validation_split(dataset, folds=4):
    transposed_dataset = dataset.T
    dataset_split = list()
    dataset_copy = list(transposed_dataset)
    fold_size = int(len(transposed_dataset) / folds)
    for i in range(folds):
        fold = list()
        while len(fold) < fold_size:
            index = np.random.randint(0,(len(dataset_copy)))
            fold.append(dataset_copy.pop(index))
        dataset_split.append(fold)
        
    dataset_split = np.array(dataset_split)
    detransposed_split = np.swapaxes(dataset_split, 1, 2)
    return detransposed_split

In [58]:
len(autoencoder_X_int)

8

In [17]:
folds = cross_validation_split(autoencoder_X_int)

In [74]:
print(folds)
print(folds.shape)
print(folds[0].shape)

[[[1 0 0 ... 0 1 0]
  [0 0 1 ... 1 1 0]
  [1 1 0 ... 1 1 0]
  ...
  [0 0 1 ... 0 1 1]
  [0 1 1 ... 1 1 1]
  [0 0 0 ... 1 1 0]]

 [[1 0 0 ... 0 1 1]
  [0 0 1 ... 0 0 1]
  [0 1 0 ... 0 0 0]
  ...
  [1 1 0 ... 0 1 1]
  [1 0 1 ... 0 0 1]
  [0 0 0 ... 0 0 0]]

 [[1 1 0 ... 1 0 1]
  [0 1 0 ... 1 1 1]
  [1 0 0 ... 1 0 1]
  ...
  [0 0 1 ... 0 0 1]
  [0 1 0 ... 0 1 0]
  [0 1 1 ... 1 0 1]]

 [[0 0 1 ... 1 1 0]
  [1 0 0 ... 0 0 0]
  [0 0 0 ... 0 1 0]
  ...
  [1 0 0 ... 1 0 1]
  [0 1 1 ... 0 0 0]
  [0 1 0 ... 1 0 0]]]
(4, 8, 250)
(8, 250)


I am looking at shape of all the folds and the first fold and it looks to be correct. I'm seeing an array with 1s and 0s. Additionally, there should be fours folds, each of which should have 8 (number of values per example) x 250 (1000 examples divided by 4 folds).

Now, I have to decide on an evaluation metric--for ease, I'm going to pick accuracy, or what percentage of predictions equal my output. Since it's only correct if the prediction equals the ground-truth by the tiniest margin, I lose some nuance, i.e. 0.999 would be counted wrong even though it's basically 1, but I can accept this limitation as it becomes tricky to decide where the threshold/cutoff (i.e. should 0.998 be correct? What about 0.990? What about 0.7?) with a toy autoencoder problem. That said, if I decide later on that I want to adjust the threshold, I can use the np.isclose to pick different margin of errors between the two values.

In [20]:
# Calculate accuracy percentage between two lists
def accuracy_metric(actual, predicted, threshold=1e-08):
    correct = np.isclose(actual, predicted, rtol=threshold, atol=threshold)
    return correct.mean() * 100

In [110]:
accuracy_metric(test_int, answers)

25.0

In [21]:
accuracy_avg = []
for i, fold in enumerate(folds): #loop through each fold
    training_set = np.delete(folds, i, axis=0).reshape(8, 250*3) #training set are all the folds except the test fold (fold[i])
    parameters = nn_model(training_set, training_set, 3, 100000, print_cost=True) #train NN with the training set
    predicted = predict(parameters, folds[i]) #predict your answers for the test fold using your trained NN
    accuracy = accuracy_metric(folds[i], predicted) #calculate accuracy
    accuracy_avg.append(accuracy) #append accuracy to a list of all the accuracies
print("The accuracy on each of the folds is:",accuracy_avg) #print the accuracy for each of the folds
print("The mean accuracy of my model is:",np.mean(accuracy_avg)) #calculate average accuracy overall

Cost after iteration 0: 5.544928
Cost after iteration 10000: 3.148037
Cost after iteration 20000: 3.051171
Cost after iteration 30000: 3.003092
Cost after iteration 40000: 2.972017
Cost after iteration 50000: 2.949496
Cost after iteration 60000: 2.932061
Cost after iteration 70000: 2.917966
Cost after iteration 80000: 2.906215
Cost after iteration 90000: 2.899255
Cost after iteration 0: 5.545022
Cost after iteration 10000: 3.108594
Cost after iteration 20000: 3.059149
Cost after iteration 30000: 3.041684
Cost after iteration 40000: 3.027895
Cost after iteration 50000: 3.015579
Cost after iteration 60000: 3.005281
Cost after iteration 70000: 2.996854
Cost after iteration 80000: 2.989836
Cost after iteration 90000: 2.983875
Cost after iteration 0: 5.545303
Cost after iteration 10000: 3.173270
Cost after iteration 20000: 3.116948
Cost after iteration 30000: 3.096189
Cost after iteration 40000: 3.084359
Cost after iteration 50000: 3.075562
Cost after iteration 60000: 3.066309
Cost after it

This is a very low accuracy, which I'm not especially surprised by given how much I was expecting perfect matches. In order to be a bit more lenient, I will modify my accuracy metric to consider answers that are off by +/- 0.15 to still be "correct." Additionally, to improve my model slightly (but keeping in mind how long it takes to run), I will run for 120,000 epochs instead of 100,000.

In [22]:
accuracy_avg = []
for i, fold in enumerate(folds): #loop through each fold
    training_set = np.delete(folds, i, axis=0).reshape(8, 250*3)
    parameters = nn_model(training_set, training_set, 3, 120000, print_cost=True)
    predicted = predict(parameters, folds[i])
    accuracy = accuracy_metric(folds[i], predicted, 0.15)
    accuracy_avg.append(accuracy)
print("The accuracy on each of the folds is:",accuracy_avg)
print("The mean accuracy of my model is:",np.mean(accuracy_avg))

Cost after iteration 0: 5.544928
Cost after iteration 10000: 3.148037
Cost after iteration 20000: 3.051171
Cost after iteration 30000: 3.003092
Cost after iteration 40000: 2.972017
Cost after iteration 50000: 2.949496
Cost after iteration 60000: 2.932061
Cost after iteration 70000: 2.917966
Cost after iteration 80000: 2.906215
Cost after iteration 90000: 2.899255
Cost after iteration 100000: 2.893360
Cost after iteration 110000: 2.888209
Cost after iteration 0: 5.545022
Cost after iteration 10000: 3.108594
Cost after iteration 20000: 3.059149
Cost after iteration 30000: 3.041684
Cost after iteration 40000: 3.027895
Cost after iteration 50000: 3.015579
Cost after iteration 60000: 3.005281
Cost after iteration 70000: 2.996854
Cost after iteration 80000: 2.989836
Cost after iteration 90000: 2.983875
Cost after iteration 100000: 2.978729
Cost after iteration 110000: 2.974228
Cost after iteration 0: 5.545303
Cost after iteration 10000: 3.173270
Cost after iteration 20000: 3.116948
Cost afte

This accuracy of ~50% is more acceptable to me, although not great. I think I could improve this more if I was willing to run more epochs.

However, I now realize that I misunderstood the instructions--it wants me to be able to reconstruct an 8x8 IDENTITY MATRIX, not necessarily run this extra evaluation. I will see how my neural net performs on an identity matrix after being trained on 120,000 epochs and my autoencoder_X_int training dataset.

In [23]:
final_autoencoder_params = nn_model(autoencoder_X_int, autoencoder_X_int, 3, 120000, print_cost=True)

Cost after iteration 0: 5.545267
Cost after iteration 10000: 3.162339
Cost after iteration 20000: 3.061024
Cost after iteration 30000: 3.010675
Cost after iteration 40000: 2.978036
Cost after iteration 50000: 2.954299
Cost after iteration 60000: 2.935858
Cost after iteration 70000: 2.920898
Cost after iteration 80000: 2.908385
Cost after iteration 90000: 2.898364
Cost after iteration 100000: 2.891053
Cost after iteration 110000: 2.884528


In [30]:
identity_matrix = np.array([[1, 0, 0, 0, 0, 0, 0, 0],
                          [0, 1, 0, 0, 0, 0, 0, 0],
                          [0, 0, 1, 0, 0, 0, 0, 0],
                          [0, 0, 0, 1, 0, 0, 0, 0],
                          [0, 0, 0, 0, 1, 0, 0, 0],
                          [0, 0, 0, 0, 0, 1, 0, 0],
                          [0, 0, 0, 0, 0, 0, 1, 0],
                           [0, 0, 0, 0, 0, 0, 0, 1]])
print(identity_matrix)

[[1 0 0 0 0 0 0 0]
 [0 1 0 0 0 0 0 0]
 [0 0 1 0 0 0 0 0]
 [0 0 0 1 0 0 0 0]
 [0 0 0 0 1 0 0 0]
 [0 0 0 0 0 1 0 0]
 [0 0 0 0 0 0 1 0]
 [0 0 0 0 0 0 0 1]]


In [36]:
answers = predict(final_autoencoder_params, test_int)
print("Autoencoder thinks the answer is:",answers)
print("The ground-truth is:",test_int)

Autoencoder thinks the answer is: [[0.99998987]
 [0.53329991]
 [1.        ]
 [0.52774607]
 [0.06069324]
 [0.4791376 ]
 [1.        ]
 [0.00526253]]
The ground-truth is: [[1]
 [0]
 [1]
 [0]
 [0]
 [0]
 [1]
 [0]]


In [32]:
identity_matrix_predicted = predict(final_autoencoder_params, identity_matrix[0])
print("Autoencoder thinks the answer is:",identity_matrix_predicted.astype(int))

Autoencoder thinks the answer is: [[0 0 0]
 [0 0 0]
 [0 0 0]
 [0 0 0]
 [0 0 0]
 [0 0 0]
 [0 0 0]
 [0 0 0]]


In [117]:
test = [1, 3, 2, 4]
np.delete(test, 1)

array([1, 2, 4])

Below are attempts to preprocess my positive training data

In [ ]:
pathway = os.path.join('./data', 'rap1-lieb-positives.txt')
train = np.loadtxt(os.path.abspath(pathway), dtype=str)
train[0]

In [ ]:
len(train)

In [ ]:
###one-hot encoding all training examples and flattening into matrix of shape (length of sequence*length of onehot vector, m)


# define universe of possible input values
alphabet = 'ACTG'
# define a mapping of chars to integers
char_to_int = dict((c, i) for i, c in enumerate(alphabet))
int_to_char = dict((i, c) for i, c in enumerate(alphabet))


#X = np.zeros((17*4, len(train)))
X = []
for sequence in train:
    # integer encode input data
    integer_encoding = [char_to_int[char] for char in sequence]
    # one hot encode
    onehot_encoding = []
    for value in integer_encoding:
        letter = [0 for _ in range(len(alphabet))]
        letter[value] = 1
        onehot_encoding.append(letter)
    final_onehot = list(itertools.chain(*onehot_encoding))
    X.append(final_onehot)
X = np.array(X)

In [ ]:
print(X)

In [ ]:
print(X.shape)
print(X[:,5].shape)

In [ ]:
Y = X #for an autoencoder

In [ ]:
optimized_parameters = nn_model(X, Y, 3)

In [ ]:
optimized_parameters

In [ ]:
predict(optimized_parameters, X[:,5]).astype(int)

In [ ]:
X[:,5]